In [1]:
import gym
import numpy as np
import random
import itertools
from sklearn import preprocessing
from IPython.display import clear_output
from gym import utils
from gym.envs.toy_text import discrete
import pandas as pd
import pymongo
from pymongo import MongoClient
from collections import defaultdict
import matplotlib
import sys

#Variabili DB
connection = MongoClient('localhost', 27017)
db = connection.Sensors
collection = db.steps_bmi
training_collection = db.training_set
test_collection = db.test_set

db_env = connection.Environments
environment_collection = db_env.env06
#env01: 5-7gg, no max reward, incremento delta bmi superiore all'1%, taglio 5% code
#env02 7-10gg, no max reward, incremento delta bmi superiore all'1%, taglio 5% code
#env03 5-7gg, no max reward, incremento unitario per variazioni di bmi superiore all'1%, taglio 5% code
#env04 7-10gg, no max reward, incremento unitario per variazioni di bmi superiore all'1%, taglio 5% code

#env05: 5-7gg, incremento unitario per variazioni di bmi superiore all'1%, taglio 5% code, standardizzazione dei dati
#env06: 5-7gg, incremento unitario per variazioni di bmi superiore all'1%, taglio 5% code, media dei valori bmi da comparare
#env07: 5-7gg, incremento delta bmi superiore all'1%, taglio 5% code, media dei valori bmi da comparare

#env08: come ... con 1/3 dei dati per il training
#env09: come ... con 2/3 dei dati per il training
#env10: come ... con 4 bin per ogni stato
#env11: come ... con 2 bin per ogni stato

#Variabili per il windowing dei dati
minimum_bmi_interval = 5
maximum_bmi_interval = 7
days_interval = 6


#Variabili per il binning
num_bins_steps = 5
num_bins_bmi = 5

#Variabili per il cutting dei dati
lower_percentile = 5
higher_percentile = 95

#Variabili per il reinforcement Learning
max_reward = 1000
min_reward = -1000

#Variabili threshold
min_bmi_variation_percentage  = 1
weekly_actions_threshold = 0.5
min_significative_steps = 1000
#recommendation_threshold = 0.7

#max_users = (len(training_collection.find().distinct("User_id")) // 3)*2
#print(max_users)

In [2]:
#Take a list of Object with "Date" attribute (d-m-y format) and return the list ordered by date
def mergeSortByDate(dated_list):
    #print("Splitting ",dateList)
    if len(dated_list)>1:
        mid = len(dated_list)//2
        lefthalf = dated_list[:mid]
        righthalf = dated_list[mid:]

        mergeSortByDate(lefthalf)
        mergeSortByDate(righthalf)

        i=0
        j=0
        k=0
        while i < len(lefthalf) and j < len(righthalf):
            ymd_left_half = lefthalf[i]["Date"].split("-")
            ymd_right_half = righthalf[j]["Date"].split("-")
            if(ymd_left_half[0] == ymd_right_half[0]):
                if(ymd_left_half[1] == ymd_right_half[1]):
                    if(int(ymd_left_half[2]) < int(ymd_right_half[2])):
                        dated_list[k]=lefthalf[i]
                        i=i+1
                    else:
                        dated_list[k]=righthalf[j]
                        j=j+1
                else:
                    if(int(ymd_left_half[1]) < int(ymd_right_half[1])):
                        dated_list[k]=lefthalf[i]
                        i=i+1
                    else:
                        dated_list[k]=righthalf[j]
                        j=j+1
            else:
                if(int(ymd_left_half[0]) < int(ymd_right_half[0])):
                    dated_list[k]=lefthalf[i]
                    i=i+1
                else:
                    dated_list[k]=righthalf[j]
                    j=j+1
            k=k+1

        while i < len(lefthalf):
            dated_list[k]=lefthalf[i]
            i=i+1
            k=k+1

        while j < len(righthalf):
            dated_list[k]=righthalf[j]
            j=j+1
            k=k+1
    #print("Merging ",dateList)
    
    return dated_list

def mergeSortByValue(dated_list):
    if len(dated_list)>1:
        mid = len(dated_list)//2
        lefthalf = dated_list[:mid]
        righthalf = dated_list[mid:]

        mergeSort(lefthalf)
        mergeSort(righthalf)

        i=0
        j=0
        k=0
        while i < len(lefthalf) and j < len(righthalf):
            if lefthalf[i]["Value"] < righthalf[j]["Value"]:
                dated_list[k]=lefthalf[i]
                i=i+1
            else:
                dated_list[k]=righthalf[j]
                j=j+1
            k=k+1

        while i < len(lefthalf):
            dated_list[k]=lefthalf[i]
            i=i+1
            k=k+1

        while j < len(righthalf):
            dated_list[k]=righthalf[j]
            j=j+1
            k=k+1
            
    return dated_list
    

#Take a list of Dates and return the list sorted
def mergeSortDates(dateList):
    #print("Splitting ",dateList)
    if len(dateList)>1:
        mid = len(dateList)//2
        lefthalf = dateList[:mid]
        righthalf = dateList[mid:]

        mergeSortDates(lefthalf)
        mergeSortDates(righthalf)

        i=0
        j=0
        k=0
        while i < len(lefthalf) and j < len(righthalf):
            ymd_left_half = lefthalf[i].split("-")
            ymd_right_half = righthalf[j].split("-")
            if(ymd_left_half[0] == ymd_right_half[0]):
                if(ymd_left_half[1] == ymd_right_half[1]):
                    if(int(ymd_left_half[2]) < int(ymd_right_half[2])):
                        dateList[k]=lefthalf[i]
                        i=i+1
                    else:
                        dateList[k]=righthalf[j]
                        j=j+1
                else:
                    if(int(ymd_left_half[1]) < int(ymd_right_half[1])):
                        dateList[k]=lefthalf[i]
                        i=i+1
                    else:
                        dateList[k]=righthalf[j]
                        j=j+1
            else:
                if(int(ymd_left_half[0]) < int(ymd_right_half[0])):
                    dateList[k]=lefthalf[i]
                    i=i+1
                else:
                    dateList[k]=righthalf[j]
                    j=j+1
            k=k+1

        while i < len(lefthalf):
            dateList[k]=lefthalf[i]
            i=i+1
            k=k+1

        while j < len(righthalf):
            dateList[k]=righthalf[j]
            j=j+1
            k=k+1
    #print("Merging ",dateList)
    return dateList


def extractValues(object_list):
    values_list = []
    for obj in object_list:
        value = obj['Value']
        values_list.append(value)
    return values_list


def getValueByDate(dated_values_list, date):
    for obj in dated_values_list:
        if(obj["Date"] == date):
            return obj["Value"]
    return -1


#Take a list of dated values objects and return the indices of valid values beetween a minimum and maximum date interval
def getValidIndices(dated_values_list, starting_window_index, dates):
    if((starting_window_index + minimum_bmi_interval) > len(dates)):
        return -1
    else:
        done = False
        while not done:
            while getValueByDate(dated_values_list, dates[starting_window_index]) == -1:
                starting_window_index += 1
                if((starting_window_index + minimum_bmi_interval) > len(dates)):
                    return -1

            ending_window_index = starting_window_index + (minimum_bmi_interval-1)

            while getValueByDate(dated_values_list, dates[ending_window_index]) == -1 and (ending_window_index - starting_window_index) < (maximum_bmi_interval-1):
                ending_window_index += 1
                if(ending_window_index >= len(dates)):
                    return -1

            if(getValueByDate(dated_values_list, dates[ending_window_index]) != -1):
                   done = True
            else:
                   starting_window_index += 1
    
    return (starting_window_index, ending_window_index)           
        
    
    
#Function that take a list of dated values and return the binned values    
def getBins(dated_values_list, num_bins, quartile = True):
    values = []
    date_bins_list = []
    for obj in dated_values_list:
        values.append(obj["Value"])
    if(quartile):
        labels = pd.qcut(values, num_bins, duplicates = "drop").codes
    else:
        labels = pd.cut(values, num_bins, duplicates = "drop").codes
    for i in range(len(dated_values_list)):
        date_bins_list.append({"Date": dated_values_list[i]["Date"], "Value": labels[i]})
    return date_bins_list


def standardize(dated_values_list):
    values = []
    standardized_dated_values = []
    for obj in dated_values_list:
        values.append(obj["Value"])
    values = np.array(values).reshape(-1, 1)
    scaler = preprocessing.StandardScaler()
    values = scaler.fit_transform(values)
    values = list(values.reshape(1,-1)[0])
    for i in range(len(dated_values_list)):
        standardized_dated_values.append({"Date": dated_values_list[i]["Date"], "Value": values[i]})
    return standardized_dated_values
        


def getvaluesByDateInterval(dated_values_list, date_list):
    interval_values = []
    for date in date_list:
        value = getValueByDate(dated_values_list, date)
        if(value == -1):
            return -1
        else:
            interval_values.append(value)
    return interval_values


#Encode a stutus(a list of bins) in a number
def encode(state):
    code = 0
    for i in range(len(state)-1):
        code += state[i] 
        code *= num_bins_steps
    code += state[len(state)-1]
    return code


def decode(code):
    out = []
    for i in range(days_interval):
        out.append(code % num_bins_steps)
        code = code // num_bins_steps
    assert 0 <= code < num_bins_steps
    return out[::-1]



def nextState(encoded_state, action):
    next_state = []
    decoded_state = decode(encoded_state)
    for bin_ in decoded_state[1:]:
        next_state.append(bin_)
    next_state.append(action)
    return encode(next_state)



def getDates():
    dates = mergeSortDates(collection.find().distinct("Date"))
    return dates



def cutTails(dated_values_list):
    #print("Cutting")
    cutted_list = []
    values = np.array(extractValues(dated_values_list))
    lower = np.percentile(values, lower_percentile)
    higher = np.percentile(values, higher_percentile)
    for obj in dated_values_list:
        if(obj["Value"]> lower and obj["Value"]<higher):
            cutted_list.append(obj)
    return cutted_list


def getMean(bmi_values, dates, date_index):
    pivot = getValueByDate(bmi_values, dates[date_index])
    #print("Pivot: ", pivot)
    if(pivot != -1):
        left = getValueByDate(bmi_values, dates[date_index-1])
        if(date_index == len(dates)-1):
            right = -1
        else:
            right = getValueByDate(bmi_values, dates[date_index+1])
        #print("Left: ", left, " Right: ", right)
        if(left != -1 and right != -1):
            return (pivot+left+right)/3
        elif(left != -1 or right != -1):
            if(left != -1):
                return (left+pivot)/2
            else:
                return (right+pivot)/2
        else:
            return pivot
    else:
        return -1


def retrieve(dataset, cleaning):
    #print("Retrieving da ", dataset)
    users_steps = {}
    users_bmi = {}
    cursor = dataset.find()
    #cursor = collection.find({"User_id":  {"$in": [ "2bc16eda651db5936cd31e735c815296fc1579d9", "4b9150ccb6ca42e0aa43824c8ddcb28e326ab467", "ce96039ca66a9b98f97b202c177cf0ef7d4aa97d" ]}})
    
    for doc in cursor:
        #print(doc)
        user_id = doc["User_id"]
        value = doc["Value"]
        date = doc["Date"]
        data_type = doc["Data_type"]
        if(data_type == 1):
            if(cleaning == "minimum_steps"):
                
                if(value < min_significative_steps):
                    print("Valore sotto la soglia")
                    continue
        
            if(user_id in users_steps):
                users_steps[user_id].append({"Date": date, "Value": value})
            else: 
                users_steps[user_id] = [{"Date": date, "Value": value}]
        elif(data_type == 3):
            if(user_id in users_bmi):
                users_bmi[user_id].append({"Date": date, "Value": value})
            else: 
                users_bmi[user_id] = [{"Date": date, "Value": value}]
    
    #print("Users steps: ", users_steps)
    #print("Users bmi: ", users_bmi)
    return users_steps, users_bmi
    

    
#
#Funzione per costruire gli stati e le azioni dell'environment
#

def buildEnv(dataset = training_collection, bmi_binning = False, cleaning = "cut", reward_policy = "unit", standard = False, bmi_mean = False):
    P = {}
    nS = num_bins_steps**days_interval
    nA = num_bins_steps

    P = {s : {a : [(1.0 , nextState(s,a), 0, False)] for a in range(nA)} for s in range(nS)}
    
    dates = getDates()

    users_steps, users_bmi = retrieve(dataset, cleaning)

    users_count = 0 

    for user in users_bmi:
        #if(users_count == max_users):
            #break
        
        if(user not in users_steps or len(users_steps[user]) < num_bins_steps):
            continue
        if(bmi_binning == True):
            if(len(users_bmi[user]) < num_bins_bmi):
                continue
        
        #print("----------User ", user, "-----------")
        users_count += 1
        starting_window_index = days_interval
        
        steps_values = users_steps[user]
        if(cleaning == "cut"):
            steps_values = cutTails(steps_values)
        if(standard == True):
            steps_values = standardize(steps_values)
        steps_bins_values = getBins(mergeSortByDate(steps_values), num_bins_steps)
        
        bmi_values = mergeSortByDate(users_bmi[user])
        if(bmi_binning == True):
            bmi_values = getBins(bmi_values, num_bins_bmi, quartile = True)
        #print("Bins degli steps: ", steps_bins_values)
        #print("\nBins dei bmi: ", bmi_bins_values)
        finished = False
        
        while not finished:
            window_dates_indices = getValidIndices(bmi_values, starting_window_index, dates)
            if(window_dates_indices == -1):
                #print("Utente processato")
                finished = True
            else:
                #print(window_dates_indices)
                starting_date_index = window_dates_indices[0]
                starting_date = dates[starting_date_index]
                
                ending_date_index = window_dates_indices[1]
                ending_date = dates[ending_date_index]
                
                old_bmi = getValueByDate(bmi_values, starting_date) 
                future_bmi = getValueByDate(bmi_values, ending_date)
                if(bmi_mean == True):
                    old_bmi = getMean(bmi_values, dates, starting_date_index)
                    future_bmi = getMean(bmi_values, dates, ending_date_index)
                
                #print("Old BMI: ", old_bmi, " Future BMI: ", future_bmi)
                
                if(bmi_binning == True):
                    reward = (old_bmi - future_bmi)/2
                    #print("\nReward ", reward)
                else:
                    delta = old_bmi - future_bmi
                    if((100*abs(delta))/old_bmi < min_bmi_variation_percentage):
                        #print("Non c'è variazione superiore al ", min_bmi_variation_percentage, "%")
                        reward = 0
                    else:
                        #print("Variazione significativa")
                        if(reward_policy == "delta"):
                            reward = delta
                        elif(reward_policy == "unit"):
                            if(delta >0):
                                reward = 1
                            elif(delta<0):
                                reward = -1

                #print("Reward: ", reward)
                
                if(reward != 0):
                    starting_index = starting_date_index - (days_interval)
                    ending_index = starting_date_index
                    
                    tmp = {}
                    actions_counter = 0
                    while ending_index <= ending_date_index:
                        interval = dates[starting_index:ending_index+1]
                        weekly_steps = getvaluesByDateInterval(steps_bins_values, interval)
                        if(weekly_steps == -1):
                            starting_index += 1
                            ending_index += 1
                            continue
                        else:
                            state = encode(weekly_steps[:days_interval])
                            action = weekly_steps[days_interval:][0]
                            nextstate = encode(weekly_steps[1:])
                            actions_counter += 1
                            #print("State ", decode(state), " Action: ", action)
                            if(state in tmp):
                                if(action not in tmp[state]):
                                    tmp[state][action] = [(1.0, nextstate, reward, False)]
                                else:
                                    prev_reward = tmp[state][action][0][2]
                                    tmp[state][action] = [(1.0, nextstate, prev_reward + reward, False)]
                    
                            else:
                                tmp[state] = {action : [(1.0, nextstate, reward, False)]}
                    
                    
                            starting_index += 1
                            ending_index += 1
                    
                    #print("Actions_counter: ", actions_counter)
                    if(actions_counter/(ending_date_index-starting_date_index+1) > weekly_actions_threshold):
                        #print("Actions counter superiore alla soglia")
                        for state in tmp:
                            for action in tmp[state]:
                                prev_reward = P[state][action][0][2]
                                tmp_reward = tmp[state][action][0][2]
                                nextstate = P[state][action][0][1]
                                P[state][action] = [(1.0, nextstate, prev_reward + tmp_reward, False)]
                
                starting_window_index = ending_date_index
        
        
    '''
    for s in P:
        actions = P[s]
        print("\n\nStato: ", decode(s), ":")
        for a in actions:
            p, n_s, r, d = P[s][a][0]
            
            if(r > max_reward):
                P[s][a] = [(p, n_s, max_reward, d)]
            elif(r < min_reward):
                P[s][a] = [(p, n_s, min_reward, d)]
            
            print("       Action: ", a, ", Probability: ", p , ", Next state: ", decode(n_s), ", Reward: ", P[s][a][0][2])
    '''
    print(users_count)
    return P

In [8]:
Ptest = buildEnv(bmi_mean = True)

Retrieving da  Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'Sensors'), 'training_set')
old_bmi prima:  29.05  e future_bmi prima:  28.94
in getMean
Pivot:  29.05
Left:  28.88  Right:  29.03
in getMean
Pivot:  28.94
Left:  -1  Right:  28.73
old_bmi dopo:  28.986666666666668 future_bmi dopo:  28.835
old_bmi prima:  28.94  e future_bmi prima:  28.32
in getMean
Pivot:  28.94
Left:  -1  Right:  28.73
in getMean
Pivot:  28.32
Left:  -1  Right:  28.21
old_bmi dopo:  28.835 future_bmi dopo:  28.265
old_bmi prima:  28.32  e future_bmi prima:  28.71
in getMean
Pivot:  28.32
Left:  -1  Right:  28.21
in getMean
Pivot:  28.71
Left:  28.23  Right:  -1
old_bmi dopo:  28.265 future_bmi dopo:  28.47
old_bmi prima:  28.65  e future_bmi prima:  28.54
in getMean
Pivot:  28.65
Left:  -1  Right:  28.45
in getMean
Pivot:  28.54
Left:  -1  Right:  28.74
old_bmi dopo:  28.549999999999997 future_bmi dopo:  28.64
old_bmi prima:  28.54  e future_bm

Left:  24.14  Right:  24.63
in getMean
Pivot:  24.2
Left:  24.64  Right:  24.12
old_bmi dopo:  24.33 future_bmi dopo:  24.320000000000004
old_bmi prima:  24.2  e future_bmi prima:  24.63
in getMean
Pivot:  24.2
Left:  24.64  Right:  24.12
in getMean
Pivot:  24.63
Left:  24.58  Right:  24.55
old_bmi dopo:  24.320000000000004 future_bmi dopo:  24.586666666666662
old_bmi prima:  24.63  e future_bmi prima:  24.4
in getMean
Pivot:  24.63
Left:  24.58  Right:  24.55
in getMean
Pivot:  24.4
Left:  24.31  Right:  24.17
old_bmi dopo:  24.586666666666662 future_bmi dopo:  24.293333333333333
old_bmi prima:  24.4  e future_bmi prima:  24.59
in getMean
Pivot:  24.4
Left:  24.31  Right:  24.17
in getMean
Pivot:  24.59
Left:  24.6  Right:  24.41
old_bmi dopo:  24.293333333333333 future_bmi dopo:  24.53333333333333
old_bmi prima:  24.59  e future_bmi prima:  24.1
in getMean
Pivot:  24.59
Left:  24.6  Right:  24.41
in getMean
Pivot:  24.1
Left:  24.16  Right:  24.35
old_bmi dopo:  24.53333333333333 fut

old_bmi dopo:  35.43 future_bmi dopo:  35.3
old_bmi prima:  35.5  e future_bmi prima:  35.41
in getMean
Pivot:  35.5
Left:  -1  Right:  -1
in getMean
Pivot:  35.41
Left:  -1  Right:  35.66
old_bmi dopo:  35.5 future_bmi dopo:  35.535
old_bmi prima:  34.96  e future_bmi prima:  36.06
in getMean
Pivot:  34.96
Left:  -1  Right:  34.59
in getMean
Pivot:  36.06
Left:  -1  Right:  -1
old_bmi dopo:  34.775000000000006 future_bmi dopo:  36.06
old_bmi prima:  36.06  e future_bmi prima:  35.12
in getMean
Pivot:  36.06
Left:  -1  Right:  -1
in getMean
Pivot:  35.12
Left:  34.95  Right:  34.99
old_bmi dopo:  36.06 future_bmi dopo:  35.02
old_bmi prima:  35.12  e future_bmi prima:  34.74
in getMean
Pivot:  35.12
Left:  34.95  Right:  34.99
in getMean
Pivot:  34.74
Left:  35.1  Right:  34.56
old_bmi dopo:  35.02 future_bmi dopo:  34.800000000000004
old_bmi prima:  34.74  e future_bmi prima:  35.01
in getMean
Pivot:  34.74
Left:  35.1  Right:  34.56
in getMean
Pivot:  35.01
Left:  -1  Right:  -1
old_

Pivot:  28.97
Left:  29.15  Right:  28.88
old_bmi dopo:  28.99 future_bmi dopo:  29.0
old_bmi prima:  28.97  e future_bmi prima:  29.12
in getMean
Pivot:  28.97
Left:  29.15  Right:  28.88
in getMean
Pivot:  29.12
Left:  -1  Right:  -1
old_bmi dopo:  29.0 future_bmi dopo:  29.12
old_bmi prima:  28.94  e future_bmi prima:  28.81
in getMean
Pivot:  28.94
Left:  -1  Right:  -1
in getMean
Pivot:  28.81
Left:  -1  Right:  28.69
old_bmi dopo:  28.94 future_bmi dopo:  28.75
old_bmi prima:  28.81  e future_bmi prima:  28.28
in getMean
Pivot:  28.81
Left:  -1  Right:  28.69
in getMean
Pivot:  28.28
Left:  -1  Right:  -1
old_bmi dopo:  28.75 future_bmi dopo:  28.28
old_bmi prima:  28.28  e future_bmi prima:  28.52
in getMean
Pivot:  28.28
Left:  -1  Right:  -1
in getMean
Pivot:  28.52
Left:  -1  Right:  28.33
old_bmi dopo:  28.28 future_bmi dopo:  28.424999999999997
old_bmi prima:  28.52  e future_bmi prima:  28.15
in getMean
Pivot:  28.52
Left:  -1  Right:  28.33
in getMean
Pivot:  28.15
Left: 

old_bmi prima:  33.58  e future_bmi prima:  33.41
in getMean
Pivot:  33.58
Left:  -1  Right:  33.52
in getMean
Pivot:  33.41
Left:  33.2  Right:  -1
old_bmi dopo:  33.55 future_bmi dopo:  33.305
old_bmi prima:  33.41  e future_bmi prima:  33.21
in getMean
Pivot:  33.41
Left:  33.2  Right:  -1
in getMean
Pivot:  33.21
Left:  -1  Right:  -1
old_bmi dopo:  33.305 future_bmi dopo:  33.21
old_bmi prima:  33.21  e future_bmi prima:  33.83
in getMean
Pivot:  33.21
Left:  -1  Right:  -1
in getMean
Pivot:  33.83
Left:  -1  Right:  33.49
old_bmi dopo:  33.21 future_bmi dopo:  33.66
old_bmi prima:  33.83  e future_bmi prima:  33.61
in getMean
Pivot:  33.83
Left:  -1  Right:  33.49
in getMean
Pivot:  33.61
Left:  -1  Right:  -1
old_bmi dopo:  33.66 future_bmi dopo:  33.61
old_bmi prima:  33.61  e future_bmi prima:  34.02
in getMean
Pivot:  33.61
Left:  -1  Right:  -1
in getMean
Pivot:  34.02
Left:  33.68  Right:  33.79
old_bmi dopo:  33.61 future_bmi dopo:  33.830000000000005
old_bmi prima:  34.02

old_bmi prima:  24.56  e future_bmi prima:  25.14
in getMean
Pivot:  24.56
Left:  -1  Right:  24.22
in getMean
Pivot:  25.14
Left:  -1  Right:  -1
old_bmi dopo:  24.39 future_bmi dopo:  25.14
old_bmi prima:  25.03  e future_bmi prima:  24.55
in getMean
Pivot:  25.03
Left:  -1  Right:  -1
in getMean
Pivot:  24.55
Left:  25.17  Right:  -1
old_bmi dopo:  25.03 future_bmi dopo:  24.86
old_bmi prima:  24.55  e future_bmi prima:  24.94
in getMean
Pivot:  24.55
Left:  25.17  Right:  -1
in getMean
Pivot:  24.94
Left:  -1  Right:  25.14
old_bmi dopo:  24.86 future_bmi dopo:  25.04
old_bmi prima:  24.94  e future_bmi prima:  24.76
in getMean
Pivot:  24.94
Left:  -1  Right:  25.14
in getMean
Pivot:  24.76
Left:  25.28  Right:  -1
old_bmi dopo:  25.04 future_bmi dopo:  25.020000000000003
old_bmi prima:  25.13  e future_bmi prima:  24.51
in getMean
Pivot:  25.13
Left:  -1  Right:  24.83
in getMean
Pivot:  24.51
Left:  -1  Right:  24.75
old_bmi dopo:  24.979999999999997 future_bmi dopo:  24.63000000

old_bmi dopo:  23.66 future_bmi dopo:  23.61
old_bmi prima:  23.61  e future_bmi prima:  23.35
in getMean
Pivot:  23.61
Left:  -1  Right:  -1
in getMean
Pivot:  23.35
Left:  -1  Right:  -1
old_bmi dopo:  23.61 future_bmi dopo:  23.35
old_bmi prima:  23.35  e future_bmi prima:  23.17
in getMean
Pivot:  23.35
Left:  -1  Right:  -1
in getMean
Pivot:  23.17
Left:  -1  Right:  -1
old_bmi dopo:  23.35 future_bmi dopo:  23.17
old_bmi prima:  23.1  e future_bmi prima:  22.96
in getMean
Pivot:  23.1
Left:  -1  Right:  -1
in getMean
Pivot:  22.96
Left:  -1  Right:  -1
old_bmi dopo:  23.1 future_bmi dopo:  22.96
old_bmi prima:  22.96  e future_bmi prima:  23.07
in getMean
Pivot:  22.96
Left:  -1  Right:  -1
in getMean
Pivot:  23.07
Left:  -1  Right:  -1
old_bmi dopo:  22.96 future_bmi dopo:  23.07
old_bmi prima:  23.07  e future_bmi prima:  23.0
in getMean
Pivot:  23.07
Left:  -1  Right:  -1
in getMean
Pivot:  23.0
Left:  -1  Right:  -1
old_bmi dopo:  23.07 future_bmi dopo:  23.0
old_bmi prima:  

IndexError: list index out of range

In [21]:
#
#Funzione che memorizza l'insieme degli stati-azioni in mongo
#
def storeEnvironment():
    P = buildEnv()
    for state in P:
        for action in P[state]:
            p, n_s, reward, done = P[state][action][0]
            doc = {"State": int(state),
                   "Action": int(action),
                   "Probability": float(p),
                   "Next_state": int(n_s),
                   "Reward": float(reward),
                   "Done": done
                    }
            environment_collection.insert_one(doc)

In [22]:
storeEnvironment()

6726


In [3]:
#
#L'environment vero e proprio
#
class HRSEnv(discrete.DiscreteEnv):
    
    def __init__(self):
        P = {}
        nS = num_bins_steps**days_interval
        nA = num_bins_steps
        isd = np.zeros(nS)
        
        cursor = environment_collection.find()
        for doc in cursor:
            state = doc["State"]
            action = doc["Action"]
            prob = doc["Probability"]
            next_state = doc["Next_state"]
            reward = doc["Reward"]
            done = doc["Done"]
            if(state in P):
                P[state][action] = [(prob, next_state, reward, done)]
                
            else:
                P[state] = {action: [(prob, next_state, reward, done)]}
                isd[state] += 1
            
        '''
        for s in P:
            ac = P[s]
            print("\n\nStato: ", decode(s), ":")
            for a in ac:
                p, nst, re, d = P[s][a][0]
                print("       Action: ", a, ", Next state: ", decode(nst), ", Reward: ", re)

        '''
        isd /= isd.sum()
        discrete.DiscreteEnv.__init__(self, nS, nA, P, isd)
    
class HRSEnvTest(discrete.DiscreteEnv):
    
    def __init__(self):
        P = buildEnv()
        #P = Ptest
        nS = num_bins_steps**days_interval
        nA = num_bins_steps
        isd = np.zeros(nS)
            
        
        for s in P:
            ac = P[s]
            isd[s] += 1
            print("\n\nStato: ", decode(s), ":")
        
            for a in ac:
                p, nst, re, d = P[s][a][0]
                print("       Action: ", a, ", Next state: ", decode(nst), ", Reward: ", re)
    
        
        isd /= isd.sum()
        discrete.DiscreteEnv.__init__(self, nS, nA, P, isd)

In [4]:
envTest = HRSEnv()
#envTest = HRSEnvTest()

In [5]:
#Algoritmo di q_learning
def make_epsilon_greedy_policy(Q, epsilon, nA):
    """
    Creates an epsilon-greedy policy based on a given Q-function and epsilon.
    
    Args:
        Q: A dictionary that maps from state -> action-values.
            Each value is a numpy array of length nA (see below)
        epsilon: The probability to select a random action . float between 0 and 1.
        nA: Number of actions in the environment.
    
    Returns:
        A function that takes the observation as an argument and returns
        the probabilities for each action in the form of a numpy array of length nA.
    
    """
    def policy_fn(observation):
        A = np.ones(nA, dtype=float) * epsilon / nA
        best_action = np.argmax(Q[observation])
        A[best_action] += (1.0 - epsilon)
        return A
    return policy_fn

def q_learning(env, num_episodes, num_explorations , discount_factor=1.0, alpha=0.5, epsilon=0.1):
    """
    Q-Learning algorithm: Off-policy TD control. Finds the optimal greedy policy
    while following an epsilon-greedy policy
    
    Args:
        env: OpenAI environment.
        num_episodes: Number of episodes to run for.
        discount_factor: Gamma discount factor.
        alpha: TD learning rate.
        epsilon: Chance the sample a random action. Float betwen 0 and 1.
    
    Returns:
        A tuple (Q, episode_lengths).
        Q is the optimal action-value function, a dictionary mapping state -> action values.
        stats is an EpisodeStats object with two numpy arrays for episode_lengths and episode_rewards.
    """
    
    # The final action-value function.
    # A nested dictionary that maps state -> (action -> action-value).
    Q = defaultdict(lambda: np.zeros(env.action_space.n))

    # Keeps track of useful statistics
    stats = plotting.EpisodeStats(
        episode_lengths=np.zeros(num_episodes),
        episode_rewards=np.zeros(num_episodes))    
    
    # The policy we're following
    policy = make_epsilon_greedy_policy(Q, epsilon, env.action_space.n)
    
    for i_episode in range(num_episodes):
        # Print out which episode we're on, useful for debugging.
        if (i_episode + 1) % 100 == 0:
            print("\rEpisode {}/{}.".format(i_episode + 1, num_episodes), end="")
            sys.stdout.flush()
        
        # Reset the environment and pick the first action
        state = env.reset()
        
        # One step in the environment
        # total_reward = 0.0
        for t in range(num_explorations):
            
            # Take a step
            action_probs = policy(state)
            action = np.random.choice(np.arange(len(action_probs)), p=action_probs)
            next_state, reward, done, _ = env.step(action)

            # Update statistics
            #stats.episode_rewards[i_episode] += reward
            #stats.episode_lengths[i_episode] = t
            
            # TD Update
            best_next_action = np.argmax(Q[next_state])    
            td_target = reward + discount_factor * Q[next_state][best_next_action]
            td_delta = td_target - Q[state][action]
            Q[state][action] += alpha * td_delta
                
            #if done:
                #break
                
            state = next_state
    
    return Q


#Altro algoritmo di q_learning
def QL(env, num_episodes, num_explorations, alpha = 0.1, gamma = 0.6, epsilon = 0.2):

    q_table = np.zeros([env.observation_space.n, env.action_space.n])

    # For plotting metrics
    #all_epochs = []
    #all_penalties = []

    #state = env.reset()
    for i in range(1,num_episodes+1):
        state = env.reset()
        for j in range(1, num_explorations+1):

            #epochs, penalties, reward, = 0, 0, 0
            #done = False

            #while not done:
            if random.uniform(0, 1) < epsilon:
                action = env.action_space.sample() # Explore action space
            else:
                action = np.argmax(q_table[state]) # Exploit learned values

            next_state, reward, done, info = env.step(action) 

            old_value = q_table[state, action]
            next_max = np.max(q_table[next_state])

            new_value = (1 - alpha) * old_value + alpha * (reward + gamma * next_max)
            q_table[state, action] = new_value

            #if reward == -10:
                #penalties += 1

            state = next_state
            #epochs += 1

        if i % 100 == 0:
            #clear_output(wait=True)
            print(f"Episode: {i}")

    print("Training finished.\n")
    
    '''
    for s in range(len(q_table)):
        print("\nState:", decode(s))
        print("Actions: ")
        for a in range(len(q_table[s])):
            print("       ", a, ": ", q_table[s][a] )
    '''        
            
    return q_table

In [46]:
q_table = QL(envTest, 1000, 100000, alpha = 0.6, gamma = 0.6, epsilon = 0.2)
#q_table = q_learning(envTest, 1000, 50000, discount_factor = 0.6, alpha = 0.2, epsilon = 0.2)

Episode: 1000
Training finished.


State: [0, 0, 0, 0, 0, 0]
Actions: 
        0 :  -0.1913815040001003
        1 :  8.01436416
        2 :  4.0163011968
        3 :  2.0791357986255576
        4 :  3.402710485423494

State: [0, 0, 0, 0, 0, 1]
Actions: 
        0 :  5.839174079999999
        1 :  8.3572736
        2 :  3.175737599999998
        3 :  3.3388495359999992
        4 :  5.12617856

State: [0, 0, 0, 0, 0, 2]
Actions: 
        0 :  6.693835328
        1 :  5.583176691729323
        2 :  3.615999999999999
        3 :  1.406572680394482
        4 :  5.235121069923668

State: [0, 0, 0, 0, 0, 3]
Actions: 
        0 :  4.4251803135999985
        1 :  4.682696691729323
        2 :  4.191934712756027
        3 :  3.0342719999999996
        4 :  6.798559999999997

State: [0, 0, 0, 0, 0, 4]
Actions: 
        0 :  0.509042590953672
        1 :  2.4890037042854516
        2 :  0.9224609522990247
        3 :  3.3814862689438563
        4 :  5.671199999999995

State: [0, 0, 0, 0, 1, 0]
Act

Actions: 
        0 :  4.183839999999998
        1 :  -0.46273572487149695
        2 :  1.8886077224215903
        3 :  6.120415999999999
        4 :  5.380959999999998

State: [0, 0, 0, 2, 0, 3]
Actions: 
        0 :  1.0811803130639217
        1 :  1.4765818293200237
        2 :  1.7794320097041036
        3 :  -2.4002984049100804
        4 :  2.374559999999998

State: [0, 0, 0, 2, 0, 4]
Actions: 
        0 :  2.162662021185535
        1 :  2.1195486965759893
        2 :  1.1438297599997944
        3 :  1.6414375464919795
        4 :  7.311199999999998

State: [0, 0, 0, 2, 1, 0]
Actions: 
        0 :  6.06437969924812
        1 :  3.7959567999999977
        2 :  2.2666053119999985
        3 :  2.1159359999999987
        4 :  1.8667199999999984

State: [0, 0, 0, 2, 1, 1]
Actions: 
        0 :  6.624774079999998
        1 :  4.1281599999999985
        2 :  2.1186627968
        3 :  2.6127023001599987
        4 :  3.6701785599999965

State: [0, 0, 0, 2, 1, 2]
Actions: 
        0 :  1.32

        2 :  3.6785055252097307
        3 :  1.839021272268491
        4 :  5.849119999999997

State: [0, 0, 0, 3, 4, 1]
Actions: 
        0 :  0.6340591272055378
        1 :  2.398551612405717
        2 :  3.5058495999999986
        3 :  4.044255999999999
        4 :  3.556866639673901

State: [0, 0, 0, 3, 4, 2]
Actions: 
        0 :  3.1136188799999998
        1 :  1.0182962694571245
        2 :  1.5168075144450286
        3 :  3.077713404166709
        4 :  1.907329083629875

State: [0, 0, 0, 3, 4, 3]
Actions: 
        0 :  3.312018848389985
        1 :  1.2907620252419423
        2 :  -2.263946785498752
        3 :  3.7651033599999986
        4 :  1.8630654578997379

State: [0, 0, 0, 3, 4, 4]
Actions: 
        0 :  5.773471999999998
        1 :  3.743199999999999
        2 :  4.5668159999999975
        3 :  2.635065599999999
        4 :  9.995999999999995

State: [0, 0, 0, 4, 0, 0]
Actions: 
        0 :  2.4979436090225553
        1 :  3.69382707312915
        2 :  4.16537122605792

        4 :  2.547147542519708

State: [0, 0, 1, 0, 2, 4]
Actions: 
        0 :  2.944671999999999
        1 :  2.1095999999999977
        2 :  3.8590868377599996
        3 :  2.1638975999999994
        4 :  0.7901657599999985

State: [0, 0, 1, 0, 3, 0]
Actions: 
        0 :  1.6533438659704673
        1 :  3.243365930431282
        2 :  0.9564339396346667
        3 :  3.108282861063956
        4 :  1.8541805483158957

State: [0, 0, 1, 0, 3, 1]
Actions: 
        0 :  -0.6221725811469297
        1 :  2.251664447999999
        2 :  1.9367466977638745
        3 :  2.1089314024719403
        4 :  1.4218247795280172

State: [0, 0, 1, 0, 3, 2]
Actions: 
        0 :  1.7355455999999987
        1 :  2.8663962495291218
        2 :  1.4384959999873248
        3 :  3.312361113599999
        4 :  5.694559999999997

State: [0, 0, 1, 0, 3, 3]
Actions: 
        0 :  2.4522722890391218
        1 :  2.0537496145919993
        2 :  3.626169599999999
        3 :  0.3335873038332915
        4 :  2.1078449

        1 :  2.6721444479999996
        2 :  3.5171491377807187
        3 :  5.04663497424896
        4 :  2.224152166807876

State: [0, 0, 1, 2, 1, 3]
Actions: 
        0 :  1.9604837182636028
        1 :  3.0574502399999988
        2 :  2.887729244159998
        3 :  3.039126067199999
        4 :  6.337759999999998

State: [0, 0, 1, 2, 1, 4]
Actions: 
        0 :  1.5763896353710067
        1 :  4.52424985583542
        2 :  -0.21512239234909042
        3 :  2.77539479465933
        4 :  5.171999999999995

State: [0, 0, 1, 2, 2, 0]
Actions: 
        0 :  3.549364799999999
        1 :  1.456042496
        2 :  3.4845759963829153
        3 :  2.3378818523122877
        4 :  4.1387199999999975

State: [0, 0, 1, 2, 2, 1]
Actions: 
        0 :  3.4935740799999984
        1 :  5.749543201279998
        2 :  3.4115013314764786
        3 :  3.5739455999999983
        4 :  2.2998976617340876

State: [0, 0, 1, 2, 2, 2]
Actions: 
        0 :  4.370745599995992
        1 :  4.850718606847999
   

...

        0 :  1.4345531006689085
        1 :  1.9545791999972213
        2 :  0.7696173410491354
        3 :  2.7565799731199983
        4 :  4.017759999999997

State: [4, 4, 3, 2, 1, 4]
Actions: 
        0 :  4.096671999999999
        1 :  2.839199996066387
        2 :  1.0183255371264908
        3 :  3.378156371888068
        4 :  4.291999999999989

State: [4, 4, 3, 2, 2, 0]
Actions: 
        0 :  2.7576911918086093
        1 :  1.2598104684257607
        2 :  2.484558718031383
        3 :  2.7889795810631677
        4 :  2.898719999999998

State: [4, 4, 3, 2, 2, 1]
Actions: 
        0 :  6.240031999999998
        1 :  1.7753791999999984
        2 :  5.094495999999996
        3 :  0.3557619199999993
        4 :  2.4774616131993206

State: [4, 4, 3, 2, 2, 2]
Actions: 
        0 :  4.035231999999999
        1 :  1.9707186038485125
        2 :  3.239999999963727
        3 :  2.4159742228426704
        4 :  0.8915481074869627

State: [4, 4, 3, 2, 2, 3]
Actions: 
        0 :  2.36485109693

        3 :  3.0263024308729936
        4 :  4.299999999999997

State: [4, 4, 3, 4, 0, 2]
Actions: 
        0 :  3.0800319999999983
        1 :  2.336697599999998
        2 :  0.9692620328959994
        3 :  2.4801987071999996
        4 :  5.204959999999998

State: [4, 4, 3, 4, 0, 3]
Actions: 
        0 :  5.557860395207948
        1 :  2.454407015482499
        2 :  4.697229776895998
        3 :  2.265035552460799
        4 :  2.950559999988619

State: [4, 4, 3, 4, 0, 4]
Actions: 
        0 :  2.7558719999999983
        1 :  2.4953525759999993
        2 :  1.3038297599999993
        3 :  3.0550584832
        4 :  7.015199999999995

State: [4, 4, 3, 4, 1, 0]
Actions: 
        0 :  3.5805691839275
        1 :  2.047199965964366
        2 :  -0.01713355908254144
        3 :  1.4224232697825008
        4 :  1.5135281938337994

State: [4, 4, 3, 4, 1, 1]
Actions: 
        0 :  4.156337553436413
        1 :  2.6776747556203437
        2 :  2.434772531794899
        3 :  4.561055999999998
   

        0 :  2.535772415999999
        1 :  1.3286591999999984
        2 :  2.1757817425919983
        3 :  2.346335999999998
        4 :  4.593119999999997

State: [4, 4, 4, 0, 4, 1]
Actions: 
        0 :  2.098654771199999
        1 :  0.8225599999999984
        2 :  6.11288428759892
        3 :  4.540255999999998
        4 :  3.211603199999999

State: [4, 4, 4, 0, 4, 2]
Actions: 
        0 :  2.324101595135999
        1 :  2.891746744319999
        2 :  3.173049599999999
        3 :  2.650876446719999
        4 :  0.43878882795519925

State: [4, 4, 4, 0, 4, 3]
Actions: 
        0 :  2.0826365668490356
        1 :  1.7668787097599992
        2 :  2.9575359999999984
        3 :  3.425097472
        4 :  2.7586372096

State: [4, 4, 4, 0, 4, 4]
Actions: 
        0 :  2.3094719999999977
        1 :  5.000953599999997
        2 :  1.5663477657599993
        3 :  6.918815999999998
        4 :  11.691999999999993

State: [4, 4, 4, 1, 0, 0]
Actions: 
        0 :  -0.6475200000000048
        

        3 :  4.493420120784895
        4 :  4.947359999999996

State: [4, 4, 4, 2, 2, 4]
Actions: 
        0 :  1.7005488279551995
        1 :  2.8537535999999895
        2 :  2.1390868377599945
        3 :  4.289757951999999
        4 :  3.7735999445069544

State: [4, 4, 4, 2, 3, 0]
Actions: 
        0 :  1.8146050559999993
        1 :  1.799059199999999
        2 :  2.9085759999999983
        3 :  1.6330283519999993
        4 :  1.6535231999999989

State: [4, 4, 4, 2, 3, 1]
Actions: 
        0 :  2.7047615999999994
        1 :  3.8424578559999985
        2 :  2.4096959999999976
        3 :  0.8620960255999996
        4 :  5.0871999999999975

State: [4, 4, 4, 2, 3, 2]
Actions: 
        0 :  2.3951552409599994
        1 :  1.6463935999999983
        2 :  3.3898784125593515
        3 :  1.0308031999999994
        4 :  3.310559999999997

State: [4, 4, 4, 2, 3, 3]
Actions: 
        0 :  0.2603199999999992
        1 :  3.884527359999999
        2 :  5.008671999999999
        3 :  9.1581759

Actions: 
        0 :  3.561145599999999
        1 :  3.1799964159999994
        2 :  3.7782586984652795
        3 :  7.936415999999998
        4 :  1.7295292308480001

State: [4, 4, 4, 4, 1, 3]
Actions: 
        0 :  4.890324735999998
        1 :  2.971858999296
        2 :  4.200735999999997
        3 :  5.7435839999999985
        4 :  3.3137599999999976

State: [4, 4, 4, 4, 1, 4]
Actions: 
        0 :  2.3526719999999983
        1 :  7.079199999999997
        2 :  3.386809599999998
        3 :  2.991740159999999
        4 :  6.219999999999997

State: [4, 4, 4, 4, 2, 0]
Actions: 
        0 :  -0.3264973414400012
        1 :  5.529977599999999
        2 :  2.2685759999999986
        3 :  0.49582105599999915
        4 :  3.775705855999999

State: [4, 4, 4, 4, 2, 1]
Actions: 
        0 :  3.534367200768
        1 :  2.4310473215999995
        2 :  1.889094053157273
        3 :  3.6269017599999986
        4 :  5.804563199999999

State: [4, 4, 4, 4, 2, 2]
Actions: 
        0 :  1.42970159

In [6]:
def policyMaker(dataset = training_collection, policy = "popular", cleaning= "cut", bmi_mean = False):
    P = {}
    table = np.zeros([num_bins_steps**days_interval, num_bins_steps])
    
    dates = getDates()
    
    users_steps, users_bmi = retrieve(dataset, cleaning)
    
    users_count = 0 
    
    if(policy == "popular"):
        table = most_popular_actions(users_steps, dates, table, cleaning)
    elif(policy == "statistical"):
        table = statistically_better_actions(users_steps, users_bmi, dates, table, cleaning, bmi_mean)
    
    return table
    
    
    
def most_popular_actions(users_steps, dates, table, cleaning):
    for user in users_steps:
        starting_index = 0
        ending_index = days_interval
        
        steps_values = users_steps[user]
        #print("Passi: ", steps_values)
        if(cleaning == "cut"):
            steps_values = cutTails(steps_values)
        steps_bins_values = getBins(mergeSortByDate(steps_values), num_bins_steps)
        
        while ending_index < len(dates):
            interval = dates[starting_index:ending_index+1]
            #print("Intervallo: ", interval)
            weekly_steps = getvaluesByDateInterval(steps_bins_values, interval)
            if(weekly_steps == -1):
                starting_index += 1
                ending_index += 1
                continue
            else:
                state = encode(weekly_steps[:days_interval])
                action = weekly_steps[days_interval:][0]
                #print("State: ", decode(state), ", Action: ", action)
                table[state, action] += 1
                starting_index += 1
                ending_index += 1
    
    #print(table)
    return table
                

    
                
def statistically_better_actions(users_steps, users_bmi, dates, table, cleaning, bmi_mean ,bmi_binning = False):
    for user in users_bmi:
        
        if(user not in users_steps):
            continue
            
        if(len(users_bmi[user]) < num_bins_bmi or len(users_steps[user]) < num_bins_steps ):
            continue
        starting_window_index = days_interval
        steps_values = users_steps[user]
        if(cleaning == "cut"):
            steps_values = cutTails(steps_values)
        steps_bins_values = getBins(mergeSortByDate(steps_values), num_bins_steps)
        bmi_values = mergeSortByDate(users_bmi[user])
        if(bmi_binning == True):
            bmi_values = getBins(bmi_values, num_bins_bmi)
        #print("Bins degli steps: ", steps_bins_values)
        #print("\nBins dei bmi: ", bmi_bins_values)
        finished = False
        
        while not finished:
            window_dates_indices = getValidIndices(bmi_values, starting_window_index, dates)
            if(window_dates_indices == -1):
                #print("Finished a user")
                finished = True
            else:
                #print(window_dates_indices)
                starting_date_index = window_dates_indices[0]
                starting_date = dates[starting_date_index]
                ending_date_index = window_dates_indices[1]
                ending_date = dates[ending_date_index]
                old_bmi = getValueByDate(bmi_values, starting_date) 
                future_bmi = getValueByDate(bmi_values, ending_date)
                if(bmi_mean == True):
                    old_bmi = getMean(bmi_values, dates, starting_date_index)
                    future_bmi = getMean(bmi_values, dates, ending_date_index)
                
                if(bmi_binning == True):
                    weight_loss = future_bmi < old_bmi
                    #print("\nReward ", reward)
                else:
                    delta = old_bmi - future_bmi
                    if((100*abs(delta))/old_bmi < min_bmi_variation_percentage):
                        weight_loss = False 
                    else:
                        weight_loss = delta > 0
                #print("Weight Loss: ", weight_loss)
                if(weight_loss):
                
                    starting_index = starting_date_index - (days_interval)
                    ending_index = starting_date_index
                    
                    tmp = {}
                    actions_counter = 0
                    while ending_index <= ending_date_index:
                        interval = dates[starting_index:ending_index+1]
                        weekly_steps = getvaluesByDateInterval(steps_bins_values, interval)
                        if(weekly_steps == -1):
                            starting_index += 1
                            ending_index += 1
                            continue
                        else:
                            actions_counter += 1
                            state = encode(weekly_steps[:days_interval])
                            #print("State: ", decode(state))
                            action = weekly_steps[days_interval:][0]
                            #print("Action: ", action)
                            if(state in tmp):
                                if(action not in tmp[state]):
                                    tmp[state][action] = 1
                                else:
                                    
                                    tmp[state][action] += 1
                                    
                            else:
                                tmp[state] = {action : 1}
                    
                            starting_index += 1
                            ending_index += 1
                    #print("Actions counter: ", actions_counter)
                    if(actions_counter/(ending_date_index-starting_date_index+1) > weekly_actions_threshold):
                        #print("Actions counter superiore alla soglia")
                        for state in tmp:
                            for action in tmp[state]:
                                table[state, action] += tmp[state][action]
                
                
                starting_window_index = ending_date_index
    
    #print(table)
    return table



def evaluatePolicy(dataset = test_collection, policy = "random", table = None, bmi_binning = False, cleaning = "cut", standard = False, bmi_mean = False):
    weight_loss_matching, weight_gain_matching, weight_loss_not_matching, weight_gain_not_matching = 0, 0, 0, 0
    
    dates = getDates()
    
    users_steps, users_bmi = retrieve(dataset, cleaning)
    
    users_count = 0
        
    for user in users_bmi:
        if(user not in users_steps):
            continue
            
        if(len(users_bmi[user]) < num_bins_bmi or len(users_steps[user]) < num_bins_steps ):
            continue
        #print("-------User ", user, "--------")    
        starting_window_index = days_interval
        steps_values = users_steps[user]
        if(cleaning == "cut"):
            steps_values = cutTails(steps_values)
        if(standard == True):
            steps_values = standardize(steps_values)
        steps_bins_values = getBins(mergeSortByDate(steps_values), num_bins_steps)
        bmi_values = mergeSortByDate(users_bmi[user])
        if(bmi_binning == True):
            bmi_values = getBins(bmi_values, num_bins_bmi)
        
        finished = False

        while not finished:
            window_dates_indices = getValidIndices(bmi_values, starting_window_index, dates)
            if(window_dates_indices == -1):
                #print("Utente processato")
                finished = True
            else:
                #print(window_dates_indices)
                starting_date_index = window_dates_indices[0]
                starting_date = dates[starting_date_index]
                ending_date_index = window_dates_indices[1]
                ending_date = dates[ending_date_index]
                old_bmi = getValueByDate(bmi_values, starting_date) 
                future_bmi = getValueByDate(bmi_values, ending_date)
                if(bmi_mean == True):
                    old_bmi = getMean(bmi_values, dates, starting_date_index)
                    future_bmi = getMean(bmi_values, dates, ending_date_index)
                
                if(bmi_binning == True):
                    weight_loss = old_bmi -future_bmi
                    #print("\nReward ", reward)
                else:
                    delta = old_bmi - future_bmi
                    if((100*abs(delta))/old_bmi < min_bmi_variation_percentage):
                        #print("Non c'è variazione superiore al ", min_bmi_variation_percentage, "%")
                        weight_loss = 0 
                    else:
                        #print("Variazione significativa")
                        weight_loss = delta
                
                #print("Weight Loss: ", weight_loss)
                if(weight_loss != 0):
                    starting_index = starting_date_index - (days_interval)
                    ending_index = starting_date_index

                    actions_counter, followed_recommendations = 0, 0

                    while ending_index <= ending_date_index:
                        interval = dates[starting_index:ending_index+1]
                        weekly_steps = getvaluesByDateInterval(steps_bins_values, interval)
                        if(weekly_steps == -1):
                            starting_index += 1
                            ending_index += 1
                            continue
                        else:
                            state = encode(weekly_steps[:days_interval])
                            #print("State: ", decode(state))
                            action = weekly_steps[days_interval:][0]
                            #print("Action: ", action)
                            nextstate = encode(weekly_steps[1:])
                            actions_counter +=1

                            #More Steps case
                            if(policy == "more_steps"):

                                if(weekly_steps[days_interval-1] < num_bins_steps-1):
                                    #suggested_actions = list(range(weekly_steps[days_interval-1] +1, num_bins_steps))
                                    suggested_actions = [weekly_steps[days_interval-1] +1]
                                else:
                                    suggested_actions = [num_bins_steps-1]

                            #Random Case
                            elif(policy == "random"):
                                suggested_actions = [random.randint(0,num_bins_steps-1)]

                            #Q_learning, Statistical, or Popular case
                            elif(policy == "q_learning" or policy == "statistical" or policy == "popular"):
                                suggested_actions = [np.argmax(table[state])]



                            #print("Suggested Action: ", suggested_actions)
                            if(action in suggested_actions):
                                #print("Followed Recommendation")
                                followed_recommendations += 1 


                            starting_index += 1
                            ending_index += 1

                    #print("Actions Counter: ", actions_counter)
                    if(actions_counter/(ending_date_index-starting_date_index+1) > weekly_actions_threshold):
                        #print("Actions Counter superiora alla soglia")
                        if(weight_loss > 0):
                            #print("Perdita di peso, setting di wlm e wlnm")
                            weight_loss_matching += followed_recommendations
                            weight_loss_not_matching += (actions_counter-followed_recommendations)
                            #print("Weight loss matching: ", weight_loss_matching)
                            #print("Weight loss not matching", weight_loss_not_matching)
                        elif(weight_loss < 0):
                            #print("Guadagno di peso, detting di wgm e wgnm")
                            weight_gain_matching += followed_recommendations
                            weight_gain_not_matching += (actions_counter-followed_recommendations)
                            #print("Weight gain matching: ", weight_gain_matching)
                            #print("Weight gain not matching: ", weight_gain_not_matching)
                
                starting_window_index = ending_date_index

        users_count += 1
    
    #print("Totatle utenti: ", users_count)
    precision = weight_loss_matching/(weight_loss_matching + weight_loss_not_matching)
    accuracy = (weight_gain_matching + weight_loss_matching)/(weight_gain_matching + weight_loss_matching + weight_loss_not_matching + weight_gain_not_matching)
    #print(policy)
    #print("Precision: ", precision, "\nAccuracy: ", accuracy)
    return precision, accuracy

In [6]:
#evaluatePolicy()
evaluatePolicy(policy = "more_steps")
#evaluatePolicy(policy = "popular", table = policyMaker(policy = "popular"))
#evaluatePolicy(policy = "statistical", table = policyMaker(policy = "statistical"))
#evaluatePolicy(policy = "q_learning", table = q_table)

Retrieving da  Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'Sensors'), 'test_set')


(0.2300201477501679, 0.22239064530099611)

In [7]:
alpha_values = [0.6]
gamma_values = [0.6]
epsilon_values = [0.2]

print("Environment: ", environment_collection)
for a in alpha_values:
    for g in gamma_values:
        for e in epsilon_values:
            q_table = QL(envTest, 1000, 100000, alpha = a, gamma = g, epsilon = e)
            prec, acc = evaluatePolicy(policy = "q_learning", table = q_table, bmi_mean = True)
            print("For Alpha = ", a, " Gamma = ", g, " ed Epsilon = ", e)
            print("Precision = ", prec)
            print("Accuracy = ", acc)
            print("\n\n\n")

Environment:  Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'Environments'), 'env06')
Episode: 100
Episode: 200
Episode: 300
Episode: 400
Episode: 500
Episode: 600
Episode: 700
Episode: 800
Episode: 900
Episode: 1000
Training finished.

For Alpha =  0.6  Gamma =  0.6  ed Epsilon =  0.2
Precision =  0.22429481346678798
Accuracy =  0.21938168846611178




